Step 2.1 – Read raw data

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

raw_path = "/Volumes/workspace/damg7370/datastore/main/la_crime/raw/"

df_raw = (spark.read
          .option("header", "true")
          .option("inferSchema", "true")
          .csv(raw_path))

df_raw.printSchema()
df_raw.show(5, truncate=False)


root
 |-- DR_NO: integer (nullable = true)
 |-- Date Rptd: string (nullable = true)
 |-- DATE OCC: string (nullable = true)
 |-- TIME OCC: integer (nullable = true)
 |-- AREA: integer (nullable = true)
 |-- AREA NAME: string (nullable = true)
 |-- Rpt Dist No: integer (nullable = true)
 |-- Part 1-2: integer (nullable = true)
 |-- Crm Cd: integer (nullable = true)
 |-- Crm Cd Desc: string (nullable = true)
 |-- Mocodes: string (nullable = true)
 |-- Vict Age: integer (nullable = true)
 |-- Vict Sex: string (nullable = true)
 |-- Vict Descent: string (nullable = true)
 |-- Premis Cd: integer (nullable = true)
 |-- Premis Desc: string (nullable = true)
 |-- Weapon Used Cd: integer (nullable = true)
 |-- Weapon Desc: string (nullable = true)
 |-- Status: string (nullable = true)
 |-- Status Desc: string (nullable = true)
 |-- Crm Cd 1: integer (nullable = true)
 |-- Crm Cd 2: integer (nullable = true)
 |-- Crm Cd 3: integer (nullable = true)
 |-- Crm Cd 4: integer (nullable = true)
 |-- L

NULL COUNT

In [0]:
from pyspark.sql.functions import col, sum as _sum, when, trim

null_counts = df_raw.select([
    _sum(
        when(col(c).isNull() | (trim(col(c)) == ""), 1).otherwise(0)
    ).alias(c)
    for c in df_raw.columns
])

display(null_counts)



DR_NO Date Rptd DATE OCC TIME OCC AREA AREA NAME Rpt Dist No Part 1-2 Crm Cd Crm Cd Desc Mocodes Vict Age Vict Sex Vict Descent Premis Cd Premis Desc Weapon Used Cd Weapon Desc Status Status Desc Crm Cd 1 Crm Cd 2 Crm Cd 3 Crm Cd 4 LOCATION Cross Street LAT LON 0 0 0 0 0 0 0 0 0 0 151619 0 144644 144656 16 588 677744 677744 1 0 11 935831 1002677 1004927 0 850755 0 0

Distinct counts (dimension candidates)

In [0]:
# STEP 1.3 – Distinct values per column (to find dimensions)

distinct_counts = df_raw.agg(
    *[countDistinct(col(c)).alias(c) for c in df_raw.columns]
)

display(distinct_counts)


DR_NO Date Rptd DATE OCC TIME OCC AREA AREA NAME Rpt Dist No Part 1-2 Crm Cd Crm Cd Desc Mocodes Vict Age Vict Sex Vict Descent Premis Cd Premis Desc Weapon Used Cd Weapon Desc Status Status Desc Crm Cd 1 Crm Cd 2 Crm Cd 3 Crm Cd 4 LOCATION Cross Street LAT LON 1004991 1896 1879 1439 21 21 1210 2 140 140 310940 104 5 20 314 306 79 79 6 6 142 126 38 6 66566 10413 5426 4982

Range / quality checks

In [0]:
# STEP 1.4.a – Date range
df_dates = df_raw.select(
    to_timestamp("DATE OCC", "yyyy MMM dd hh:mm:ss a").alias("date_occ"),
    to_timestamp("Date Rptd", "yyyy MMM dd hh:mm:ss a").alias("date_rptd")
)

df_dates.select(
    min("date_occ").alias("min_date_occ"),
    max("date_occ").alias("max_date_occ"),
    min("date_rptd").alias("min_date_rptd"),
    max("date_rptd").alias("max_date_rptd")
).show(truncate=False)


+-------------------+-------------------+-------------------+-------------------+
|min_date_occ       |max_date_occ       |min_date_rptd      |max_date_rptd      |
+-------------------+-------------------+-------------------+-------------------+
|2020-01-01 00:00:00|2025-05-29 00:00:00|2020-01-01 00:00:00|2025-06-04 00:00:00|
+-------------------+-------------------+-------------------+-------------------+



In [0]:
# STEP 1.4.b – Time range
df_raw.selectExpr(
    "min(`TIME OCC`) as min_time",
    "max(`TIME OCC`) as max_time"
).show()


+--------+--------+
|min_time|max_time|
+--------+--------+
|       1|    2359|
+--------+--------+



In [0]:
# STEP 1.4.c – Victim age range
df_raw.selectExpr(
    "min(`Vict Age`) as min_age",
    "max(`Vict Age`) as max_age"
).show()


+-------+-------+
|min_age|max_age|
+-------+-------+
|     -4|    120|
+-------+-------+



In [0]:
# STEP 1.4.d – LAT/LON validity
df_raw.selectExpr(
    "min(LAT) as min_lat",
    "max(LAT) as max_lat",
    "min(LON) as min_lon",
    "max(LON) as max_lon"
).show()

df_raw.filter("LAT = 0 or LON = 0").count()


+-------+-------+---------+-------+
|min_lat|max_lat|  min_lon|max_lon|
+-------+-------+---------+-------+
|    0.0|34.3343|-118.6676|    0.0|
+-------+-------+---------+-------+



2240

In [0]:
%sql
-- how many rows in fact vs raw
SELECT COUNT(*) FROM damg7370.fact_crime_incident_la;

SELECT COUNT(*) FROM damg7370.bronze_la_crime;


COUNT(*) 1004991

In [0]:
%sql
-- sample joined view
SELECT
  f.crime_incident_id,
  d.year,
  d.month_name,
  t.time_bucket,
  a.area_name,
  c.crime_desc,
  v.age_group,
  v.victim_sex,
  s.arrest_type
FROM damg7370.fact_crime_incident_la f
JOIN damg7370.dim_date_la   d ON f.date_key  = d.date_key
JOIN damg7370.dim_time_la   t ON f.time_key  = t.time_key
JOIN damg7370.dim_area_la   a ON f.area_key  = a.area_key
JOIN damg7370.dim_crime_la  c ON f.crime_key = c.crime_key
JOIN damg7370.dim_victim_la v ON f.victim_age = v.victim_age AND f.victim_sex = v.victim_sex
JOIN damg7370.dim_status_la s ON f.status_key = s.status_key
LIMIT 50;


crime_incident_id year month_name time_bucket area_name crime_desc age_group victim_sex arrest_type 211507896 2020 November Morning N Hollywood THEFT OF IDENTITY 25-44 M None 201516622 2020 October Evening N Hollywood ASSAULT WITH DEADLY WEAPON, AGGRAVATED ASSAULT 25-44 M None 240913563 2020 October Afternoon Van Nuys THEFT OF IDENTITY 25-44 M None 210704711 2020 December Afternoon Wilshire THEFT FROM MOTOR VEHICLE - GRAND ($950.01 AND OVER) 45-64 F None 201418201 2020 September Evening Pacific THEFT FROM MOTOR VEHICLE - PETTY ($950 & UNDER) 45-64 M None 240412063 2020 November Afternoon Hollenbeck THEFT OF IDENTITY 25-44 M None 240317069 2020 April Afternoon Southwest THEFT OF IDENTITY 18-24 F None 201115217 2020 July Afternoon Northeast CRM AGNST CHLD (13 OR UNDER) (14-15 & SUSP 10 YRS OLDER) 13-17 F Adult 241708596 2020 March Afternoon Devonshire THEFT OF IDENTITY 25-44 M None 242113813 2020 September Morning Topanga THEFT OF IDENTITY 45-64 M None 240605846 2020 June Night Hollywood CRM AGNST CHLD (13 OR UNDER) (14-15 & SUSP 10 YRS OLDER) 13-17 M Adult 242014110 2020 November Afternoon Olympic THEFT OF IDENTITY 25-44 F None 202113531 2020 September Afternoon Topanga VEHICLE - STOLEN 0-12 X Adult 201710725 2020 July Morning Devonshire BURGLARY 0-12 X None 201406733 2020 February Night Pacific BURGLARY FROM VEHICLE 25-44 M None 201405970 2020 February Afternoon Pacific THEFT PLAIN - PETTY ($950 & UNDER) 25-44 M Adult 201820230 2020 November Morning Southeast INTIMATE PARTNER - SIMPLE ASSAULT 25-44 F None 201707577 2020 March Afternoon Devonshire BATTERY - SIMPLE ASSAULT 18-24 F None 201514848 2020 August Night N Hollywood BURGLARY 0-12 M Adult 201405023 2020 January Evening Pacific BURGLARY 25-44 M None 211306997 2020 November Evening Newton THEFT PLAIN - PETTY ($950 & UNDER) 25-44 F None 201405778 2020 January Afternoon Pacific THEFT PLAIN - PETTY ($950 & UNDER) 25-44 M None 202005291 2020 January Morning Olympic THEFT PLAIN - PETTY ($950 & UNDER) 0-12 X None 201715737 2020 November Afternoon Devonshire BURGLARY 65+ F None 201608553 2020 April Evening Foothill ASSAULT WITH DEADLY WEAPON, AGGRAVATED ASSAULT 13-17 M Adult 202006163 2020 February Afternoon Olympic VANDALISM - MISDEAMEANOR ($399 OR UNDER) 18-24 M None 202009677 2020 May Morning Olympic VEHICLE - ATTEMPT STOLEN 25-44 M None 201915689 2020 October Night Mission VANDALISM - FELONY ($400 & OVER, ALL CHURCH VANDALISMS) 25-44 F None 201918078 2020 December Morning Mission ROBBERY 18-24 M None 202013248 2020 August Night Olympic INTIMATE PARTNER - SIMPLE ASSAULT 25-44 M Adult 202011749 2020 June Morning Olympic VANDALISM - FELONY ($400 & OVER, ALL CHURCH VANDALISMS) 45-64 M None 201811813 2020 May Night Southeast VEHICLE - STOLEN 0-12 X None 201809657 2020 April Afternoon Southeast INTIMATE PARTNER - SIMPLE ASSAULT 45-64 F None 201409975 2020 April Evening Pacific BURGLARY FROM VEHICLE 25-44 M None 201819653 2020 October Morning Southeast VANDALISM - FELONY ($400 & OVER, ALL CHURCH VANDALISMS) 18-24 F None 201911106 2020 April Evening Mission ASSAULT WITH DEADLY WEAPON, AGGRAVATED ASSAULT 18-24 M None 201819475 2020 October Night Southeast ASSAULT WITH DEADLY WEAPON, AGGRAVATED ASSAULT 25-44 M Adult 202106474 2020 February Evening Topanga ASSAULT WITH DEADLY WEAPON, AGGRAVATED ASSAULT 45-64 M None 202115676 2020 November Night Topanga BURGLARY 45-64 M None 201416348 2020 August Afternoon Pacific VEHICLE - STOLEN 0-12 X None 201420586 2020 November Morning Pacific THEFT FROM MOTOR VEHICLE - PETTY ($950 & UNDER) 25-44 F None 201504263 2020 January Afternoon N Hollywood BURGLARY FROM VEHICLE 18-24 M None 202013922 2020 August Morning Olympic THEFT PLAIN - PETTY ($950 & UNDER) 18-24 M None 201615829 2020 December Afternoon Foothill ROBBERY 0-12 M None 201908231 2020 March Evening Mission FIREARMS RESTRAINING ORDER (FIREARMS RO) 25-44 F None 220614831 2020 August Afternoon Hollywood THEFT OF IDENTITY 25-44 M None 201420127 2020 November Afternoon Pacific BIKE - STOLEN 25-44

In [0]:
%sql
SELECT * FROM damg7370.fact_crime_incident_la;



crime_incident_id area_key crime_key date_key time_key status_key weapon_key victim_age victim_sex victim_descent lat lon 211507896 15 354 2020-11-07 845 IC null 31 M H 34.2124 -118.4092 201516622 15 230 2020-10-18 1845 IC 200 32 M H 34.1993 -118.4203 240913563 9 354 2020-10-30 1240 IC null 30 M W 34.1847 -118.4509 210704711 7 331 2020-12-24 1310 IC null 47 F A 34.0339 -118.3747 201418201 14 420 2020-09-29 1830 IC null 63 M H 33.9813 -118.435 240412063 4 354 2020-11-11 1210 IC null 35 M B 34.083 -118.1678 240317069 3 354 2020-04-16 1350 IC null 21 F B 34.01 -118.29 201115217 11 812 2020-07-07 1400 AO 500 14 F H 34.1107 -118.2589 241708596 17 354 2020-03-02 1200 IC null 43 M W 34.2763 -118.521 242113813 21 354 2020-09-01 900 IC null 57 M W 34.1493 -118.5886 240605846 6 812 2020-06-20 1 AA 400 13 M H 34.0878 -118.3146 242014110 20 354 2020-11-17 1320 IC null 34 F A 34.0672 -118.3016 202113531 21 510 2020-09-05 1500 AA null 0 X null 34.1938 -118.5631 201710725 17 310 2020-07-02 500 IC null 0 X X 34.2427 -118.582 201406733 14 330 2020-02-13 2300 IC null 32 M W 34.024 -118.409 201405970 14 440 2020-02-01 1658 AO null 39 M O 33.944 -118.4073 201820230 18 626 2020-11-08 730 IC 400 26 F B 33.9383 -118.2652 201707577 17 624 2020-03-20 1320 IC 500 21 F W 34.2572 -118.5885 201514848 15 310 2020-08-17 400 AA null 0 M W 34.17 -118.3722 201405023 14 310 2020-01-19 1850 IC 500 37 M A 34.0158 -118.4258 211306997 13 440 2020-11-01 1800 IC null 37 F H 34.0283 -118.2562 201405778 14 440 2020-01-20 1540 IC null 34 M W 33.943 -118.4035 202005291 20 440 2020-01-29 545 IC null 0 X X 34.0618 -118.2891 201715737 17 310 2020-11-25 1200 IC null 69 F W 34.2467 -118.4872 201608553 16 230 2020-04-28 1730 AA 114 14 M H 34.2685 -118.4364 202006163 20 745 2020-02-11 1600 IC null 24 M H 34.0617 -118.3066 202009677 20 520 2020-05-13 900 IC null 36 M H 34.0559 -118.3142 201915689 19 740 2020-10-15 305 IC null 35 F H 34.3069 -118.4297 201918078 19 210 2020-12-15 1111 IC 114 19 M H 34.2214 -118.4677 202013248 20 626 2020-08-09 2250 AA 400 43 M H 34.0495 -118.2891 202011749 20 740 2020-06-26 700 IC null 48 M O 34.0633 -118.3141 201811813 18 510 2020-05-25 200 IC null 0 X null 33.9144 -118.2894 201809657 18 626 2020-04-15 1550 IC 400 49 F B 33.9019 -118.2893 201409975 14 330 2020-04-21 1930 IC null 43 M H 34.0056 -118.4301 201819653 18 740 2020-10-28 1000 IC null 22 F B 33.9213 -118.2847 201911106 19 230 2020-04-26 1908 IC 102 19 M H 34.2152 -118.451 201819475 18 230 2020-10-24 2250 AO 106 39 M H 33.8983 -118.2896 202106474 21 230 2020-02-24 1835 IC 400 58 M W 34.1683 -118.6007 202115676 21 310 2020-11-03 330 IC null 46 M X 34.1849 -118.5974 201416348 14 510 2020-08-28 1200 IC null 0 X null 33.9918 -118.4446 201420586 14 420 2020-11-18 630 IC null 33 F H 34.0296 -118.4306 201504263 15 330 2020-01-05 1300 IC null 23 M H 34.1867 -118.3703 202013922 20 440 2020-08-27 830 IC null 21 M B 34.0581 -118.3102 201615829 16 210 2020-12-16 1500 IC 400 0 M W 34.2139 -118.3965 201908231 19 906 2020-03-30 2000 IC null 28 F W 34.2128 -118.445 220614831 6 354 2020-08-17 1200 IC null 28 M H 34.0944 -118.3277 201420127 14 480 2020-11-08 1300 IC null 34 F O 33.9568 -118.3962 201810632 18 624 2020-05-04 1530 IC 400 18 F W 33.9602 -118.2651 202115664 21 668 2020-09-03 1400 AO null 30 M X 34.2011 -118.5713 202013106 20 440 2020-08-06 530 AO null 51 F W 34.0728 -118.3135 201908682 19 627 2020-04-12 2221 AA 400 11 M H 34.2427 -118.4702 201419812 14 740 2020-11-06 1910 IC null 48 M H 34.0039 -118.4334 210404224 4 310 2020-12-27 1130 IC null 61 F H 34.0785 -118.1661 202105280 21 420 2020-01-28 1800 IC null 0 X null 34.1683 -118.5787 201904694 19 510 2020-01-15 2130 IC null 0 X null 34.3193 -118.4871 210205056 2 354 2020-10-14 1200 IC null 37 M W 34.0656 -118.2621 202011797 20 740 2020-07-04 2030 IC null 0 X X 34.0799 -118.3113 201407385 14 330 2020-02-02 2000 IC null 31 F W 34.0086 -118.4246 211104687 11 745 2020-01-21 300 IC null 0 X X 34.0982 -118.2943 201513536 15 510 2020-08-04 730 IC nul

In [0]:
%sql
SELECT * FROM damg7370.dim_date_la;




date_key year quarter month month_name week_of_year day_of_week 2021-03-28 2021 1 3 March 12 Sunday 2022-10-28 2022 4 10 October 43 Friday 2020-03-22 2020 1 3 March 12 Sunday 2020-12-25 2020 4 12 December 52 Friday 2024-10-26 2024 4 10 October 43 Saturday 2024-11-04 2024 4 11 November 45 Monday 2020-07-01 2020 3 7 July 27 Wednesday 2023-06-12 2023 2 6 June 24 Monday 2023-04-19 2023 2 4 April 16 Wednesday 2020-05-14 2020 2 5 May 20 Thursday 2022-10-07 2022 4 10 October 40 Friday 2023-07-05 2023 3 7 July 27 Wednesday 2023-09-04 2023 3 9 September 36 Monday 2021-08-24 2021 3 8 August 34 Tuesday 2022-08-31 2022 3 8 August 35 Wednesday 2023-03-22 2023 1 3 March 12 Wednesday 2024-11-20 2024 4 11 November 47 Wednesday 2022-10-21 2022 4 10 October 42 Friday 2021-10-28 2021 4 10 October 43 Thursday 2024-11-24 2024 4 11 November 47 Sunday 2024-06-25 2024 2 6 June 26 Tuesday 2024-12-20 2024 4 12 December 51 Friday 2021-10-21 2021 4 10 October 42 Thursday 2023-01-28 2023 1 1 January 4 Saturday 2023-03-25 2023 1 3 March 12 Saturday 2023-10-29 2023 4 10 October 43 Sunday 2023-05-23 2023 2 5 May 21 Tuesday 2020-08-15 2020 3 8 August 33 Saturday 2021-12-30 2021 4 12 December 52 Thursday 2023-02-07 2023 1 2 February 6 Tuesday 2020-10-03 2020 4 10 October 40 Saturday 2021-12-05 2021 4 12 December 48 Sunday 2024-09-05 2024 3 9 September 36 Thursday 2022-08-25 2022 3 8 August 34 Thursday 2020-06-21 2020 2 6 June 25 Sunday 2021-08-21 2021 3 8 August 33 Saturday 2021-03-22 2021 1 3 March 12 Monday 2022-07-06 2022 3 7 July 27 Wednesday 2022-02-24 2022 1 2 February 8 Thursday 2023-10-21 2023 4 10 October 42 Saturday 2023-04-15 2023 2 4 April 15 Saturday 2020-12-18 2020 4 12 December 51 Friday 2022-01-02 2022 1 1 January 52 Sunday 2022-01-06 2022 1 1 January 1 Thursday 2021-01-13 2021 1 1 January 2 Wednesday 2021-02-12 2021 1 2 February 6 Friday 2020-01-30 2020 1 1 January 5 Thursday 2021-01-02 2021 1 1 January 53 Saturday 2021-01-27 2021 1 1 January 4 Wednesday 2024-03-10 2024 1 3 March 10 Sunday 2024-05-06 2024 2 5 May 19 Monday 2025-01-30 2025 1 1 January 5 Thursday 2025-03-09 2025 1 3 March 10 Sunday 2020-02-10 2020 1 2 February 7 Monday 2024-02-24 2024 1 2 February 8 Saturday 2021-03-10 2021 1 3 March 10 Wednesday 2022-09-09 2022 3 9 September 36 Friday 2024-07-30 2024 3 7 July 31 Tuesday 2020-03-14 2020 1 3 March 11 Saturday 2023-06-21 2023 2 6 June 25 Wednesday 2023-10-27 2023 4 10 October 43 Friday 2023-06-14 2023 2 6 June 24 Wednesday 2024-05-07 2024 2 5 May 19 Tuesday 2020-08-03 2020 3 8 August 32 Monday 2023-02-24 2023 1 2 February 8 Friday 2023-04-23 2023 2 4 April 16 Sunday 2020-04-14 2020 2 4 April 16 Tuesday 2020-04-29 2020 2 4 April 18 Wednesday 2024-03-03 2024 1 3 March 9 Sunday 2024-10-10 2024 4 10 October 41 Thursday 2021-03-30 2021 1 3 March 13 Tuesday 2020-11-24 2020 4 11 November 48 Tuesday 2021-08-03 2021 3 8 August 31 Tuesday 2022-01-28 2022 1 1 January 4 Friday 2024-09-25 2024 3 9 September 39 Wednesday 2021-11-06 2021 4 11 November 44 Saturday 2021-10-19 2021 4 10 October 42 Tuesday 2021-03-16 2021 1 3 March 11 Tuesday 2022-12-23 2022 4 12 December 51 Friday 2023-02-08 2023 1 2 February 6 Wednesday 2020-03-23 2020 1 3 March 13 Monday 2023-07-18 2023 3 7 July 29 Tuesday 2024-10-12 2024 4 10 October 41 Saturday 2021-06-14 2021 2 6 June 24 Monday 2021-10-15 2021 4 10 October 41 Friday 2024-11-14 2024 4 11 November 46 Thursday 2021-04-18 2021 2 4 April 15 Sunday 2020-11-03 2020 4 11 November 45 Tuesday 2023-10-16 2023 4 10 October 42 Monday 2020-05-23 2020 2 5 May 21 Saturday 2021-05-08 2021 2 5 May 18 Saturday 2021-02-08 2021 1 2 February 6 Monday 2021-02-07 2021 1 2 February 5 Sunday 2020-02-19 2020 1 2 February 8 Wednesday 2025-02-03 2025 1 2 February 6 Monday 2022-05-07 2022 2 5 May 18 Saturday 2023-11-20 2023 4 11 November 47 Monday 2024-09-12 2024 3 9 September 37 Thursday 2020-10-28 2020 4 10 October 44 Wednesday 2023-04-08 2023 2 4 April 14 Saturday 2024-01-09 2024 1 1 January 2 Tuesday 2020-08-05 2020 3 8 August 32 Wedne

In [0]:
%sql
SELECT * FROM damg7370.dim_area_la;


area_key area_name lat lon 14 Pacific 33.9629 -118.3993 18 Southeast 33.9528 -118.2869 18 Southeast 33.9601 -118.2881 21 Topanga 34.2198 -118.6003 17 Devonshire 34.2286 -118.5885 13 Newton 34.0213 -118.2535 17 Devonshire 34.2308 -118.5336 18 Southeast 33.9348 -118.2826 17 Devonshire 34.283 -118.493 17 Devonshire 34.2411 -118.5459 16 Foothill 34.252 -118.2955 18 Southeast 33.9473 -118.2652 17 Devonshire 34.2608 -118.593 16 Foothill 34.2544 -118.2898 17 Devonshire 34.2683 -118.4771 14 Pacific 33.9745 -118.4625 14 Pacific 33.9772 -118.4647 17 Devonshire 34.2482 -118.5345 16 Foothill 34.2073 -118.3508 16 Foothill 34.2632 -118.428 5 Harbor 33.7324 -118.2814 16 Foothill 34.2121 -118.4052 17 Devonshire 34.2612 -118.5146 19 Mission 34.2503 -118.4383 12 77th Street 33.9827 -118.3255 5 Harbor 33.727 -118.2884 4 Hollenbeck 34.073 -118.2007 5 Harbor 33.8657 -118.2858 10 West Valley 34.1528 -118.4972 6 Hollywood 34.1077 -118.3158 13 Newton 33.9825 -118.2695 8 West LA 34.119 -118.4482 11 Northeast 34.0938 -118.2551 11 Northeast 34.0934 -118.2974 12 77th Street 33.9708 -118.2789 5 Harbor 33.8019 -118.3074 8 West LA 34.1098 -118.4647 11 Northeast 34.0928 -118.2713 8 West LA 34.0584 -118.4216 8 West LA 34.0554 -118.4212 5 Harbor 33.7958 -118.2999 11 Northeast 34.091 -118.2788 4 Hollenbeck 34.0924 -118.1806 6 Hollywood 34.1017 -118.3561 21 Topanga 34.202 -118.6472 8 West LA 34.0466 -118.4643 17 Devonshire 34.261 -118.4772 21 Topanga 34.1696 -118.6453 5 Harbor 33.838 -118.3017 19 Mission 34.2164 -118.4372 11 Northeast 34.0869 -118.2533 8 West LA 34.0311 -118.4547 12 77th Street 34.0022 -118.3089 14 Pacific 33.9674 -118.4563 19 Mission 34.2157 -118.4297 17 Devonshire 34.2686 -118.5428 12 77th Street 33.9681 -118.3309 21 Topanga 34.1872 -118.5691 5 Harbor 33.7387 -118.2799 3 Southwest 34.017 -118.2931 17 Devonshire 34.2683 -118.4972 14 Pacific 33.9682 -118.4568 1 Central 34.0573 -118.2474 16 Foothill 34.2345 -118.3496 16 Foothill 34.2174 -118.3614 14 Pacific 33.9574 -118.4485 8 West LA 34.0755 -118.4965 18 Southeast 33.9256 -118.2604 7 Wilshire 34.0386 -118.345 16 Foothill 34.2765 -118.4089 6 Hollywood 34.1058 -118.3696 15 N Hollywood 34.1631 -118.3856 17 Devonshire 34.2896 -118.5254 16 Foothill 34.2453 -118.2683 18 Southeast 33.9438 -118.2739 13 Newton 34.015 -118.2599 21 Topanga 34.2091 -118.6176 17 Devonshire 34.2482 -118.5299 13 Newton 34.0159 -118.246 19 Mission 34.2291 -118.4657 13 Newton 34.0157 -118.2562 14 Pacific 34.0024 -118.4009 8 West LA 34.0711 -118.4454 16 Foothill 34.2809 -118.4019 14 Pacific 33.9632 -118.4209 12 77th Street 33.9906 -118.3002 2 Rampart 34.0613 -118.2598 21 Topanga 34.2282 -118.5951 14 Pacific 33.9598 -118.4136 16 Foothill 34.2108 -118.3719 20 Olympic 34.0581 -118.3174 19 Mission 34.2582 -118.4543 21 Topanga 34.202 -118.6081 20 Olympic 34.0406 -118.2906 17 Devonshire 34.2319 -118.5374 19 Mission 34.2509 -118.4544 13 Newton 34.0301 -118.2389 17 Devonshire 34.2594 -118.5951 14 Pacific 34.0002 -118.4276 12 77th Street 33.9942 -118.3061 17 Devonshire 34.2427 -118.586 12 77th Street 33.9969 -118.2959 3 Southwest 34.0219 -118.2959 12 77th Street 33.9751 -118.328 4 Hollenbeck 34.0871 -118.1929 8 West LA 34.0505 -118.4362 8 West LA 34.039 -118.4286 6 Hollywood 34.1053 -118.3158 1 Central 34.0305 -118.262 11 Northeast 34.116 -118.2956 5 Harbor 33.746 -118.2817 5 Harbor 33.7868 -118.302 1 Central 34.0432 -118.2504 7 Wilshire 34.0632 -118.3614 8 West LA 34.0571 -118.3847 8 West LA 34.0381 -118.3975 7 Wilshire 34.0444 -118.3274 3 Southwest 34.0053 -118.3447 6 Hollywood 34.089 -118.3146 2 Rampart 34.0641 -118.2481 11 Northeast 34.084 -118.2683 6 Hollywood 34.098 -118.3381 5 Harbor 33.7823 -118.2744 10 West Valley 34.1567 -118.4771 4 Hollenbeck 34.0774 -118.1749 10 West Valley 34.2011 -118.5404 1 Central 34.0388 -118.2731 3 Southwest 34.0309 -118.3067 11 Northeast 34.0854 -118.2204 4 Hollenbeck 34.0471 -118.2083 4 Hollenbeck 34.0447 -118.2265 3 Southwest 34.0341 -118.3664 5 Harbor 33.7712 -118.2748 8 West LA 34.047 -118.5259 1 Ce

In [0]:
%sql
SELECT * FROM damg7370.dim_crime_la;

crime_key crime_desc 520 VEHICLE - ATTEMPT STOLEN 924 TELEPHONE PROPERTY - DAMAGE 761 BRANDISH WEAPON 948 BIGAMY 814 CHILD PORNOGRAPHY 753 DISCHARGE FIREARMS/SHOTS FIRED 933 PROWLER 320 BURGLARY, ATTEMPTED 445 DISHONEST EMPLOYEE ATTEMPTED THEFT 654 CREDIT CARDS, FRAUD USE ($950 & UNDER 926 TRAIN WRECKING 880 DISRUPT SCHOOL 940 EXTORTION 946 OTHER MISCELLANEOUS CRIME 310 BURGLARY 353 DRUNK ROLL 668 EMBEZZLEMENT, GRAND THEFT ($950.01 & OVER) 410 BURGLARY FROM VEHICLE, ATTEMPTED 901 VIOLATION OF RESTRAINING ORDER 487 BOAT - STOLEN 943 CRUELTY TO ANIMALS 954 CONTRIBUTING 870 CHILD ABANDONMENT 950 DEFRAUDING INNKEEPER/THEFT OF SERVICES, OVER $950.01 651 DOCUMENT WORTHLESS ($200.01 & OVER) 652 DOCUMENT WORTHLESS ($200 & UNDER) 890 FAILURE TO YIELD 231 ASSAULT WITH DEADLY WEAPON ON POLICE OFFICER 451 PURSE SNATCHING - ATTEMPT 432 BLOCKING DOOR INDUCTION CENTER 345 DISHONEST EMPLOYEE - GRAND THEFT 453 DRUNK ROLL - ATTEMPT 932 PEEPING TOM 830 INCEST (SEXUAL ACTS BETWEEN BLOOD RELATIVES) 760 LEWD/LASCIVIOUS ACTS WITH CHILD 820 ORAL COPULATION 806 PANDERING 330 BURGLARY FROM VEHICLE 625 OTHER ASSAULT 235 CHILD ABUSE (PHYSICAL) - AGGRAVATED ASSAULT 763 STALKING 442 SHOPLIFTING - PETTY THEFT ($950 & UNDER) 910 KIDNAPPING 343 SHOPLIFTING-GRAND THEFT ($950.01 & OVER) 437 RESISTING ARREST 648 ARSON 664 BUNCO, PETTY THEFT 450 THEFT FROM PERSON - ATTEMPT 237 CHILD NEGLECT (SEE 300 W.I.C.) 210 ROBBERY 928 THREATENING PHONE CALLS/LETTERS 810 SEX,UNLAWFUL(INC MUTUAL CONSENT, PENETRATION W/ FRGN OBJ 922 CHILD STEALING 884 FAILURE TO DISPERSE 110 CRIMINAL HOMICIDE 471 TILL TAP - PETTY ($950 & UNDER) 331 THEFT FROM MOTOR VEHICLE - GRAND ($950.01 AND OVER) 930 CRIMINAL THREATS - NO WEAPON DISPLAYED 865 DRUGS, TO A MINOR 762 LEWD CONDUCT 121 RAPE, FORCIBLE 250 SHOTS FIRED AT MOVING VEHICLE, TRAIN OR AIRCRAFT 480 BIKE - STOLEN 122 RAPE, ATTEMPTED 813 CHILD ANNOYING (17YRS & UNDER) 433 DRIVING WITHOUT OWNER CONSENT (DWOC) 755 BOMB SCARE 434 FALSE IMPRISONMENT 474 THEFT, COIN MACHINE - PETTY ($950 & UNDER) 740 VANDALISM - FELONY ($400 & OVER, ALL CHURCH VANDALISMS) 251 SHOTS FIRED AT INHABITED DWELLING 440 THEFT PLAIN - PETTY ($950 & UNDER) 438 RECKLESS DRIVING 649 DOCUMENT FORGERY / STOLEN FELONY 436 LYNCHING - ATTEMPTED 653 CREDIT CARDS, FRAUD USE ($950.01 & OVER) 661 UNAUTHORIZED COMPUTER ACCESS 230 ASSAULT WITH DEADLY WEAPON, AGGRAVATED ASSAULT 944 CONSPIRACY 886 DISTURBING THE PEACE 666 BUNCO, ATTEMPT 662 BUNCO, GRAND THEFT 670 EMBEZZLEMENT, PETTY THEFT ($950 & UNDER) 475 THEFT, COIN MACHINE - ATTEMPT 660 COUNTERFEIT 350 THEFT, PERSON 420 THEFT FROM MOTOR VEHICLE - PETTY ($950 & UNDER) 805 PIMPING 627 CHILD ABUSE (PHYSICAL) - SIMPLE ASSAULT 622 BATTERY ON A FIREFIGHTER 349 GRAND THEFT / AUTO REPAIR 822 HUMAN TRAFFICKING - COMMERCIAL SEX ACTS 113 MANSLAUGHTER, NEGLIGENT 470 TILL TAP - GRAND THEFT ($950.01 & OVER) 485 BIKE - ATTEMPTED STOLEN 441 THEFT PLAIN - ATTEMPT 510 VEHICLE - STOLEN 956 LETTERS, LEWD - TELEPHONE CALLS, LEWD 906 FIREARMS RESTRAINING ORDER (FIREARMS RO) 949 ILLEGAL DUMPING 341 THEFT-GRAND ($950.01 & OVER)EXCPT,GUNS,FOWL,LIVESTK,PROD 821 SODOMY/SEXUAL CONTACT B/W PENIS OF ONE PERS TO ANUS OTH 452 PICKPOCKET, ATTEMPT 435 LYNCHING 352 PICKPOCKET 624 BATTERY - SIMPLE ASSAULT 647 THROWING OBJECT AT MOVING VEHICLE 951 DEFRAUDING INNKEEPER/THEFT OF SERVICES, $950 & UNDER 439 FALSE POLICE REPORT 347 GRAND THEFT / INSURANCE FRAUD 845 SEX OFFENDER REGISTRANT OUT OF COMPLIANCE 522 VEHICLE, STOLEN - OTHER (MOTORIZED SCOOTERS, BIKES, ETC) 902 VIOLATION OF TEMPORARY RESTRAINING ORDER 236 INTIMATE PARTNER - AGGRAVATED ASSAULT 443 SHOPLIFTING - ATTEMPT 942 BRIBERY 812 CRM AGNST CHLD (13 OR UNDER) (14-15 & SUSP 10 YRS OLDER) 220 ATTEMPTED ROBBERY 920 KIDNAPPING - GRAND ATTEMPT 756 WEAPONS POSSESSION/BOMBING 745 VANDALISM - MISDEAMEANOR ($399 OR UNDER) 850 INDECENT EXPOSURE 860 BATTERY WITH SEXUAL CONTACT 351 PURSE SNATCHING 446 PETTY THEFT - AUTO REPAIR 921 HUMAN TRAFFICKING - INVOLUNTARY SERVITUDE 903 CONTEMPT OF COURT 815 SEXUAL PENETRATION W/FORE

In [0]:
%sql
SELECT * FROM damg7370.dim_status_la;


status_key status_desc is_arrest_made arrest_type CC UNK 0 None JA Juv Arrest 1 Juvenile AO Adult Other 1 Adult JO Juv Other 1 Juvenile AA Adult Arrest 1 Adult null UNK 0 None IC Invest Cont 0 None

In [0]:
%sql
SELECT * FROM damg7370.dim_weapon_la;

weapon_key weapon_desc 501 BOMB THREAT 508 MARTIAL ARTS WEAPONS 504 DEMAND NOTE null null 209 STRAIGHT RAZOR 216 SCISSORS 214 ICE PICK 124 M-14 SEMIAUTOMATIC ASSAULT RIFLE 312 PIPE/METAL PIPE 205 KITCHEN KNIFE 202 BOWIE KNIFE 115 ASSAULT WEAPON/UZI/AK47/ETC 212 BOTTLE 210 RAZOR BLADE 204 FOLDING KNIFE 509 ROPE/LIGATURE 117 UNK TYPE SEMIAUTOMATIC ASSAULT RIFLE 203 DIRK/DAGGER 500 UNKNOWN WEAPON/OTHER WEAPON 515 PHYSICAL PRESENCE 208 RAZOR 223 UNKNOWN TYPE CUTTING INSTRUMENT 400 STRONG-ARM (HANDS, FIST, FEET OR BODILY FORCE) 217 SWORD 305 FIXED OBJECT 503 CAUSTIC CHEMICAL/POISON 505 EXPLOXIVE DEVICE 103 RIFLE 308 STICK 512 MACE/PEPPER SPRAY 506 FIRE 516 DOG/ANIMAL (SIC ANIMAL ON) 309 BOARD 207 OTHER KNIFE 105 SAWED OFF RIFLE/SHOTGUN 311 HAMMER 118 UZI SEMIAUTOMATIC ASSAULT RIFLE 513 STUN GUN 113 SIMULATED GUN 219 SCREWDRIVER 116 ANTIQUE FIREARM 218 OTHER CUTTING INSTRUMENT 502 BOW AND ARROW 120 MAC-11 SEMIAUTOMATIC ASSAULT WEAPON 306 ROCK/THROWN OBJECT 220 SYRINGE 107 OTHER FIREARM 307 VEHICLE 106 UNKNOWN FIREARM 104 SHOTGUN 102 HAND GUN 310 CONCRETE BLOCK/BRICK 302 BLUNT INSTRUMENT 109 SEMI-AUTOMATIC PISTOL 122 HECKLER & KOCH 93 SEMIAUTOMATIC ASSAULT RIFLE 200 KNIFE WITH BLADE 6INCHES OR LESS 304 CLUB/BAT 112 TOY GUN 114 AIR PISTOL/REVOLVER/RIFLE/BB GUN 110 SEMI-AUTOMATIC RIFLE 108 AUTOMATIC WEAPON/SUB-MACHINE GUN 125 RELIC FIREARM 123 M1-1 SEMIAUTOMATIC ASSAULT RIFLE 121 HECKLER & KOCH 91 SEMIAUTOMATIC ASSAULT RIFLE 213 CLEAVER 101 REVOLVER 301 BELT FLAILING INSTRUMENT/CHAIN 300 BLACKJACK 303 BRASS KNUCKLES 119 MAC-10 SEMIAUTOMATIC ASSAULT WEAPON 211 AXE 221 GLASS 511 VERBAL THREAT 201 KNIFE WITH BLADE OVER 6 INCHES IN LENGTH 510 SCALDING LIQUID 514 TIRE IRON 111 STARTER PISTOL/REVOLVER 206 SWITCH BLADE 215 MACHETE 507 LIQUOR/DRUGS

In [0]:
%sql
SELECT * FROM damg7370.dim_victim_la;

victim_age age_group victim_sex victim_descent 4 0-12 F H 18 18-24 M P 62 45-64 X B 51 45-64 M X 13 13-17 M O 44 25-44 F Z 37 25-44 F G 57 45-64 M B 37 25-44 F I 21 18-24 F P 34 25-44 M W 67 65+ F B 34 25-44 F X 36 25-44 F P 34 25-44 F I 21 18-24 F O 26 25-44 F U 78 65+ F A 30 25-44 F G 31 25-44 F W 32 25-44 F A 36 25-44 F O 58 45-64 F K 35 25-44 M K 56 45-64 M H 27 25-44 F I 25 25-44 F G 48 45-64 F W 79 65+ F W 0 0-12 F U 64 45-64 F V 5 0-12 F X 63 45-64 M W 62 45-64 X X 58 45-64 X X 2 0-12 M B 86 65+ F O 21 18-24 M K 2 0-12 X X 33 25-44 F H 70 65+ F A 60 45-64 M I 53 45-64 F C 53 45-64 M J 29 25-44 F A 96 65+ M B 55 45-64 X F 15 13-17 M H 57 45-64 F O 70 65+ M I 27 25-44 M S 47 45-64 X O 27 25-44 M K 67 65+ M C 27 25-44 F D 39 25-44 F O 29 25-44 M D 36 25-44 X W 25 25-44 M G 59 45-64 X W 20 18-24 F X 9 0-12 X X 65 65+ M H 24 18-24 F F 40 25-44 F A 34 25-44 X X 48 45-64 M W 67 65+ F P 45 45-64 F Z 56 45-64 X H 23 18-24 X K 16 13-17 M F 40 25-44 F O 43 25-44 F H 14 13-17 M O 16 13-17 F G 34 25-44 F O 59 45-64 F W 6 0-12 F X 71 65+ F A 57 45-64 M J 32 25-44 M S 68 65+ F C 55 45-64 F Z 97 65+ F H 55 45-64 M F 11 0-12 M O 27 25-44 M L 62 45-64 F P 37 25-44 M A 23 18-24 F W 14 13-17 M A 18 18-24 X H 56 45-64 M P 14 13-17 F J 27 25-44 F W 78 65+ F O 30 25-44 M C 9 0-12 F X 93 65+ F O 25 25-44 F D 32 25-44 M P 11 0-12 M A 73 65+ M Z 53 45-64 F X 91 65+ F X 18 18-24 X F 56 45-64 F V 32 25-44 F I 31 25-44 F B 52 45-64 M W 38 25-44 X O 40 25-44 X O 31 25-44 F A 42 25-44 M K 54 45-64 M V 93 65+ F F 5 0-12 F I 88 65+ X X 55 45-64 M H 12 0-12 M X 44 25-44 F P 97 65+ M B 32 25-44 F D 15 13-17 M B 38 25-44 X F 94 65+ F J 71 65+ M K 7 0-12 F A 67 65+ M B 56 45-64 F F 22 18-24 M F 33 25-44 M S 74 65+ M F 25 25-44 M V 22 18-24 F V 22 18-24 F U 86 65+ M K 4 0-12 M O 53 45-64 X X 0 0-12 M O 2 0-12 F C 51 45-64 F V 3 0-12 M C 61 45-64 M O 36 25-44 M X 92 65+ M C 79 65+ F J 48 45-64 X F 52 45-64 M H 95 65+ F B 70 65+ F F 73 65+ M I 26 25-44 X Z 20 18-24 X O 70 65+ M B 25 25-44 M B 59 45-64 F Z 66 65+ M F 66 65+ M I 46 45-64 M C 73 65+ F P 12 0-12 M B 29 25-44 F K 87 65+ M B 30 25-44 F I 71 65+ F F 3 0-12 F O 41 25-44 F D 30 25-44 M I 76 65+ M C 78 65+ F F 77 65+ F W 29 25-44 M G 32 25-44 M K 50 45-64 M I 85 65+ M H 63 45-64 F X 82 65+ M W 29 25-44 M J 18 18-24 M B 63 45-64 X X 49 45-64 F J 24 18-24 M Z 78 65+ M F 75 65+ F C 85 65+ M J 93 65+ F W 88 65+ F K 47 45-64 M G 26 25-44 M I 34 25-44 F A 77 65+ F A 5 0-12 M W 57 45-64 F B 6 0-12 F F 24 18-24 X X 61 45-64 X W 0 0-12 M F 33 25-44 F X 23 18-24 M J 31 25-44 X B 31 25-44 X F 79 65+ F V 44 25-44 F G 62 45-64 F O 66 65+ F H 6 0-12 M W 61 45-64 M H 23 18-24 F U 55 45-64 M V 33 25-44 X C 14 13-17 F O 73 65+ M V 74 65+ F H 33 25-44 F A 44 25-44 X O 48 45-64 M I 45 45-64 M Z 42 25-44 F A 91 65+ M A 6 0-12 F O 49 45-64 M H 28 25-44 F J 66 65+ M G 27 25-44 M J 53 45-64 F I 48 45-64 F F 32 25-44 F F 86 65+ X X 57 45-64 F H 38 25-44 M A 33 25-44 F P 25 25-44 M W 87 65+ F H 45 45-64 X W 18 18-24 M V 70 65+ X X 39 25-44 F X 60 45-64 M Z 50 45-64 M J 61 45-64 M A 16 13-17 M X 50 45-64 M A 46 45-64 F W 25 25-44 M X 63 45-64 F F 79 65+ F X 42 25-44 M C 86 65+ M B 40 25-44 F K 7 0-12 M A 25 25-44 F W 39 25-44 M B 43 25-44 M F 28 25-44 M X 49 45-64 M V 34 25-44 X W 69 65+ M J 34 25-44 M L 24 18-24 X A 68 65+ M H 67 65+ F W 48 45-64 F Z 19 18-24 F G 85 65+ F J 82 65+ F O 14 13-17 X X 98 65+ M W 75 65+ F X 16 13-17 F H 33 25-44 M I 27 25-44 X O 69 65+ M H 90 65+ M W 66 65+ F I 36 25-44 M S 28 25-44 M A 26 25-44 F W 82 65+ F F 26 25-44 F I 0 0-12 X H 33 25-44 F G 63 45-64 F Z 87 65+ X X 30 25-44 X Z 70 65+ F H 69 65+ M O 61 45-64 M C 61 45-64 X H 85 65+ F C 43 25-44 M V 67 65+ M A 27 25-44 F J 10 0-12 M F 51 45-64 F P 61 45-64 F I 42 25-44 M Z 75 65+ M V 40 25-44 M H 65 65+ F J 42 25-44 X F 55 45-64 M L 73 65+ M B 26 25-44 M A 38 25-44 X null 32 25-44 M I 22 18-24 F C 0 0-12 X A 62 45-64 F W 55 45-64 F W 27 25-44 M C 68 65+ F X 8 0-12 M A 40 25-44 X W 41 25-44 F C 30 25-44 X F 82 65+ M K 25 25-44 F B 12 0-12 M H 69